In [10]:
import os
import pandas as pd

import sys, copy
from datetime import datetime
sys.path.append('../../Scripts')

from preprocess_daily import DailyPreprocessor

from generate_signals import SignalGenerator

In [2]:
self = DailyPreprocessor()

In [3]:
self.load_data()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.


In [4]:
# 2-1-1~7
self.make_match1()
self.make_match2()
self.make_match3()
self.make_match4()
self.make_match5()
self.make_match6()
self.make_matching()

이동류정보 불러오는 중: 100%|██████████| 17280/17280 [00:15<00:00, 1138.40it/s]


In [8]:
match6 = self.match6.copy()
matching = self.matching.copy()
self.initialize_state()

2-2. 비보호우회전(g)을 배정했습니다.


In [112]:
self.match6 = match6
self.matching=matching

In [100]:
self.initialize_state()

2-2. 비보호우회전(g)을 배정했습니다.


In [101]:
self.match6

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0        175         1         A        8       남       북       179       004   
1        175         1         B        4       북       남       003       176   
2        175         2         A        7       북       동       001       095   
3        175         2         B        3       남       서       179       270   
4        175         3         A        6       동       서       090       270   
..       ...       ...       ...      ...     ...     ...       ...       ...   
3        210         2         B        2       서       동       270       090   
4        210         3         A        7       북       동       359       090   
5        210         3         B        4       북       남       000       180   
6        210         4         A        8       남       북       180       000   
7        210         4         B        3       남       서       180       270   

         inc_edge      out_edge node_id  
0   -571542797_02  571500487_01      i0  
1   -571500487_01  571542797_02      i0  
2   -571500487_01  571545870_01      i0  
3   -571542797_02  571510153_01      i0  
4    571545870_02  571510153_01      i0  
..            ...           ...     ...  
3             NaN           NaN     u60  
4             NaN           NaN     u60  
5             NaN           NaN     u60  
6             NaN           NaN     u60  
7             NaN           NaN     u60  

[116 rows x 11 columns]

In [77]:
# node = self.net.getNode(node_id)
# conns = list(node.getConnections())
# print(node_id)
# for con in node.getConnections():
#     print(con)
# print()
# for con in conns:
#     print(con)

In [71]:
all_conns = list(node.getConnections())
allocated_conns = []
# display(matching)
row = self.matching.iloc[0]
node_id = row.node_id
move_no = row.move_no
inc_edge = row.inc_edge
out_edge = row.out_edge
state = copy.deepcopy(self.node2init)[node_id]

node = self.net.getNode(node_id)

print(node_id)
print(state)
print(inc_edge)
print(out_edge)
inc_edge = self.net.getEdge(inc_edge)
out_edge = self.net.getEdge(out_edge)
# incoming edge, outgoing edge가 지정된 이동류에 대하여
for conn in inc_edge.getConnections(out_edge):
    allocated_conns.append(conns)
    print(conn)
    index = conn.getTLLinkIndex()
    if index >= 0:
        # 신호를 G로 지정
        state[index] = 'G'
print(state)
for conn in allocated_conns:
    print(conn)

i0
['g', 'r', 'r', 'r', 'g', 'r', 'r', 'r', 'g', 'r', 'r', 'r', 'r', 'r', 'g', 'r', 'r']
571545870_02
571542797_02
<connection from="571545870_02" to="571542797_02" fromLane="0" toLane="1" tl="i0" linkIndex="7" direction="l">
['g', 'r', 'r', 'r', 'g', 'r', 'r', 'G', 'g', 'r', 'r', 'r', 'r', 'r', 'g', 'r', 'r']
[<sumolib.net.connection.Connection object at 0x0000022B6D65A400>, <sumolib.net.connection.Connection object at 0x0000022B6D65A460>, <sumolib.net.connection.Connection object at 0x0000022B6D65A490>, <sumolib.net.connection.Connection object at 0x0000022B6D65A4C0>, <sumolib.net.connection.Connection object at 0x0000022B6D65AB80>, <sumolib.net.connection.Connection object at 0x0000022B6D65ABB0>, <sumolib.net.connection.Connection object at 0x0000022B6D65ABE0>, <sumolib.net.connection.Connection object at 0x0000022B6D65AC10>, <sumolib.net.connection.Connection object at 0x0000022B6D65AC40>, <sumolib.net.connection.Connection object at 0x0000022B6D65AC70>, <sumolib.net.connection.Con

In [84]:
node_id = self.node_ids[0]
node = self.net.getNode(node_id)
node

<junction id="c30"/>

In [113]:
node2conns = dict()
node2allocated_conns = dict()
for node_id in self.node_ids:
    node = self.net.getNode(node_id)
    node2conns[node_id] = list(node.getConnections())
    node2allocated_conns[node_id] = []

In [118]:
self.match6 = match6
self.matching=matching

In [119]:
self.matching['init_state'] = self.matching['node_id'].map(self.node2init)
self.matching['state'] = self.matching['init_state'].map(lambda x:''.join(x))
    
node2allocated_conns = dict()
# matching의 각 행을 순회
for row in self.matching.itertuples(index=True):
    node_id = row.node_id
    move_no = row.move_no
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    state = copy.deepcopy(self.node2init)[node_id]

    if move_no != 21:
        inc_edge = self.net.getEdge(inc_edge)
        out_edge = self.net.getEdge(out_edge)
        for conn in inc_edge.getConnections(out_edge):
            # node2allocated_conns[node_id].append(conn)
            index = conn.getTLLinkIndex()
            if index >= 0:
                state[index] = 'G'
        self.matching.at[row.Index, 'state'] = ''.join(state)

self.matching = self.matching.dropna(subset='state')
self.matching = self.matching.reset_index(drop=True)
self.matching = self.matching[['inter_no', 'node_id', 'move_no', 'state']]


i0
i0
i0
i0
i0
i0
i0
i0
i0
i0
i0
i0
i0
u00
i1
i1
i1
i1
i1
i1
i1
i1
i2
i2
i2
i2
i2
i2
i2
i2
i2
u20
i3
i3
i3
i3
i3
i3
i3
i3
i3
i3
i3
i3
i3
i3
i3
i3
u30
u31
u32
i8
i8
i8
i8
i8
i8
i8
i8
i8
i8
i8
i8
i8
i9
i9
i9
i9
i7
i7
i7
i7
i6
i6
i6
i6
i6
i6
i6
i6
i6
i6
i6
i6
u60


In [ ]:
node2allocated_conns

In [57]:
self.assign_signals()

2-3. 직진 및 좌회전(G)을 배정했습니다.


In [62]:
match6

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0        175         1         A        8       남       북       179       004   
1        175         1         B        4       북       남       003       176   
2        175         2         A        7       북       동       001       095   
3        175         2         B        3       남       서       179       270   
4        175         3         A        6       동       서       090       270   
..       ...       ...       ...      ...     ...     ...       ...       ...   
3        210         2         B        2       서       동       270       090   
4        210         3         A        7       북       동       359       090   
5        210         3         B        4       북       남       000       180   
6        210         4         A        8       남       북       180       000   
7        210         4         B        3       남       서       180       270   

         inc_edge      out_edge node_id  
0   -571542797_02  571500487_01      i0  
1   -571500487_01  571542797_02      i0  
2   -571500487_01  571545870_01      i0  
3   -571542797_02  571510153_01      i0  
4    571545870_02  571510153_01      i0  
..            ...           ...     ...  
3             NaN           NaN     u60  
4             NaN           NaN     u60  
5             NaN           NaN     u60  
6             NaN           NaN     u60  
7             NaN           NaN     u60  

[116 rows x 11 columns]

In [58]:
self.match6

inter_no node_id  phase_no ring_type  move_no              state
0         175      i0         1         A        8  grrrgrrrgGGGGrgrr
1         175      i0         1         B        4  gGGrgrrrgrrrrrgrr
2         175      i0         2         A        7  grrGgrrrgrrrrrgrr
3         175      i0         2         B        3  grrrgrrrgrrrrGgrr
4         175      i0         3         A        6  grrrgGGrgrrrrrgrr
..        ...     ...       ...       ...      ...                ...
111       210     u60         2         B        2          ggggggggr
112       210     u60         3         A        7          ggggggggr
113       210     u60         3         B        4          ggggggggr
114       210     u60         4         A        8          ggggggggr
115       210     u60         4         B        3          ggggggggr

[116 rows x 6 columns]

In [25]:
self.match6

inter_no node_id  phase_no ring_type  move_no              state
0         175      i0         1         A        8  grrrgrrrgGGGGrgrr
1         175      i0         1         B        4  gGGrgrrrgrrrrrgrr
2         175      i0         2         A        7  grrGgrrrgrrrrrgrr
3         175      i0         2         B        3  grrrgrrrgrrrrGgrr
4         175      i0         3         A        6  grrrgGGrgrrrrrgrr
..        ...     ...       ...       ...      ...                ...
111       210     u60         2         B        2          ggggggggr
112       210     u60         3         A        7          ggggggggr
113       210     u60         3         B        4          ggggggggr
114       210     u60         4         A        8          ggggggggr
115       210     u60         4         B        3          ggggggggr

[116 rows x 6 columns]